In [1]:
import pandas as pd
import matplotlib.pyplot as plt 
import numpy as np
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
import plotly.figure_factory as ff

In [2]:
# Load and prepare the dataset
df = pd.read_csv('Anti_Fraud_Centre_Data.csv')

# Clean dollar loss data
df['Dollar Loss Clean'] = df['Dollar Loss /pertes financires'].astype(str).str.replace('$', '')
df['Dollar Loss Clean'] = df['Dollar Loss Clean'].str.replace(',', '')
df['Dollar Loss Clean'] = pd.to_numeric(df['Dollar Loss Clean'], errors='coerce')
df

Numro d'identification / Number ID Date Received / Date reue  \
0                                        1                2021-01-02   
1                                        2                2021-01-02   
2                                        3                2021-01-02   
3                                        4                2021-01-02   
4                                        5                2021-01-02   
...                                    ...                       ...   
313971                              313972                2024-12-31   
313972                              313973                2024-12-31   
313973                              313974                2024-12-31   
313974                              313975                2024-12-31   
313975                              313976                2024-12-31   

       Complaint Received Type Type de plainte reue        Country  \
0                 CAFC Website        CAFC site web         Canada   
1                 CAFC Website        CAFC site web         Canada   
2                 CAFC Website        CAFC site web  Not Specified   
3                 CAFC Website        CAFC site web  United States   
4                 CAFC Website        CAFC site web         Canada   
...                        ...                  ...            ...   
313971                   Phone              Tlphone         Canada   
313972                   Phone              Tlphone         Canada   
313973                   Phone              Tlphone         Canada   
313974                   Phone              Tlphone         Canada   
313975                   Phone              Tlphone         Canada   

              Pays    Province/State         Province/tat  \
0           Canada       Nova Scotia       Nouvelle-cosse   
1           Canada  British Columbia  Colombie-Britanique   
2       Non spcifi     Not Specified           Non spcifi   
3        tats-Unis        California           Californie   
4           Canada           Ontario              Ontario   
...            ...               ...                  ...   
313971      Canada           Alberta              Alberta   
313972      Canada           Ontario              Ontario   
313973      Canada            Quebec                Qubec   
313974      Canada            Quebec                Qubec   
313975      Canada            Quebec                Qubec   

       Fraud and Cybercrime Thematic Categories  \
0                                      Phishing   
1                                Identity Fraud   
2                                       Romance   
3                           Foreign Money Offer   
4                                   Merchandise   
...                                         ...   
313971                                  Service   
313972                           Identity Fraud   
313973                                  Service   
313974                                Extortion   
313975                                  Unknown   

       Catgories thmatiques sur la fraude et la cybercriminalit  ...  \
0                                              Hameonnage        ...   
1                                       Fraude  l'identit        ...   
2                                                 Romance        ...   
3                               Offre dargent de ltranger        ...   
4                                             Marchandise        ...   
...                                                   ...        ...   
313971                                            Service        ...   
313972                                  Fraude  l'identit        ...   
313973                                            Service        ...   
313974                                          Extorsion        ...   
313975                                            Inconnu        ...   

               Gender           Genre Language of Correspondence  \
0              Female  

In [3]:
# 1. Distribution of dollar losses (Histogram with KDE)
# Filter out zero and null values for better visualization
dollar_loss_data = df[df['Dollar Loss Clean'] > 0]['Dollar Loss Clean']

fig1 = go.Figure()

# Add histogram
fig1.add_trace(go.Histogram(
    x=dollar_loss_data,
    name='Dollar Loss',
    nbinsx=50,
    marker_color='rgb(67, 147, 195)'
))

fig1.update_layout(
    title={
        'text': 'Distribution of Dollar Losses',
        'x': 0.5,
        'xanchor': 'center'
    },
    xaxis_title='Dollar Loss ($)',
    yaxis_title='Frequency',
    template='plotly_white',
    showlegend=False,
    plot_bgcolor='white',
    height=500,
    bargap=0.1
)

# Use log scale for better distribution visualization
fig1.update_xaxes(type='log', tickformat='$,.0f')

fig1.show()

In [4]:
# 2. Average dollar loss per complaint type (Bar Chart)
complaint_stats = df.groupby('Complaint Type').agg({
    'Dollar Loss Clean': ['mean', 'count', 'sum']
}).reset_index()

# Flatten column names
complaint_stats.columns = ['Complaint Type', 'Average Loss', 'Count', 'Total Loss']

# Sort by average loss and filter for types with significant cases
complaint_stats = complaint_stats[complaint_stats['Count'] >= 5]
complaint_stats = complaint_stats.sort_values('Average Loss', ascending=True)

fig2 = go.Figure()

# Add horizontal bar chart
fig2.add_trace(go.Bar(
    x=complaint_stats['Average Loss'],
    y=complaint_stats['Complaint Type'],
    orientation='h',
    marker=dict(
        color=complaint_stats['Average Loss'],
        colorscale='Viridis'
    ),
    text=complaint_stats['Count'].apply(lambda x: f'n={x}'),
    textposition='inside'
))

fig2.update_layout(
    title={
        'text': 'Average Dollar Loss by Complaint Type',
        'x': 0.5,
        'xanchor': 'center'
    },
    xaxis_title='Average Dollar Loss ($)',
    yaxis_title='Complaint Type',
    template='plotly_white',
    showlegend=False,
    plot_bgcolor='white',
    height=600,
    xaxis=dict(tickformat='$,.0f')
)

fig2.show()

In [5]:
# 3. Number of victims vs. Dollar loss (Scatter Plot)
fig3 = px.scatter(
    df[df['Dollar Loss Clean'] > 0],  # Filter out zero losses
    x='Number of Victims / Nombre de victimes',
    y='Dollar Loss Clean',
    color='Complaint Type',
    size='Dollar Loss Clean',
    size_max=30,
    opacity=0.7,
    title='Number of Victims vs. Dollar Loss',
    template='plotly_white',
    hover_data={
        'Number of Victims / Nombre de victimes': True,
        'Dollar Loss Clean': ':$,.2f',
        'Complaint Type': True
    }
)

fig3.update_layout(
    title={
        'text': 'Relationship between Number of Victims and Dollar Loss',
        'x': 0.5,
        'xanchor': 'center'
    },
    xaxis_title='Number of Victims',
    yaxis_title='Dollar Loss ($)',
    plot_bgcolor='white',
    height=600,
    legend_title='Complaint Type',
    legend=dict(
        yanchor='top',
        y=0.99,
        xanchor='left',
        x=1.02
    ),
    yaxis=dict(type='log', tickformat='$,.0f')
)

# Update marker appearance
fig3.update_traces(
    marker=dict(line=dict(width=1, color='DarkSlateGrey'))
)

fig3.show()